# HW1: Frame-Level Speech Recognition

In this homework, you will be working with MFCC data consisting of 28 features at each time step/frame. Your model should be able to recognize the phoneme occured in that frame.

# Libraries

In [ ]:
!pip install torchsummaryX==1.1.0 wandb --quiet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.7/9.7 MB 83.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 15.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 311.4/311.4 kB 22.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 4.2 MB/s eta 0:00:00


In [ ]:
import torch
import numpy as np
from torchsummaryX import summary
import sklearn
import gc
import zipfile
import pandas as pd
from tqdm.auto import tqdm
import os
import datetime
import wandb
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print("Device: ", device)

from torch.amp import GradScaler, autocast
import torchaudio
import torchaudio.transforms as T

Device:  cuda


In [ ]:
''' If you are using colab, you can import google drive to save model checkpoints in a folder
    If you want to use it, uncomment the two lines below
'''
# from google.colab import drive
# drive.mount('/content/drive')

' If you are using colab, you can import google drive to save model checkpoints in a folder\n    If you want to use it, uncomment the two lines below\n'

In [ ]:
### PHONEME LIST
PHONEMES = [
            '[SIL]',   'AA',    'AE',    'AH',    'AO',    'AW',    'AY',
            'B',     'CH',    'D',     'DH',    'EH',    'ER',    'EY',
            'F',     'G',     'HH',    'IH',    'IY',    'JH',    'K',
            'L',     'M',     'N',     'NG',    'OW',    'OY',    'P',
            'R',     'S',     'SH',    'T',     'TH',    'UH',    'UW',
            'V',     'W',     'Y',     'Z',     'ZH',    '[SOS]', '[EOS]']
PHONEMES = PHONEMES[:-2]

# Kaggle

This section contains code that helps you install kaggle's API, creating kaggle.json with you username and API key details. Make sure to input those in the given code to ensure you can download data from the competition successfully.

In [ ]:
!rm -rf /root/.kaggle

In [ ]:
!pip install --upgrade --force-reinstall --no-deps kaggle==1.5.8
!mkdir /root/.kaggle

with open("/root/.kaggle/kaggle.json", "w+") as f:
    f.write('{"username":"abhigyankishor","key":"ce53f67a6b84738c6b11d7917e02e653"}')
    # Put your kaggle username & key here

!chmod 600 /root/.kaggle/kaggle.json

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.2/59.2 kB 4.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for kaggle: filename=kaggle-1.5.8-py3-none-any.whl size=73248 sha256=d662d35f02f609c7f634e7f5aab5dc007f2a89f51b8a47828ab88159ccde594a
  Stored in directory: /root/.cache/pip/wheels/0b/76/ca/e58f8afa83166a0e68f0d5cd2e7f99d260bdc40e35da080eee
Successfully built kaggle
  Attempting uninstall: kaggle
    Found existing installation: kaggle 1.6.17
    Uninstalling kaggle-1.6.17:
      Successfully uninstalled kaggle-1.6.17


In [ ]:
!cat /root/.kaggle/kaggle.json

{"username":"abhigyankishor","key":"ce53f67a6b84738c6b11d7917e02e653"}

In [ ]:
# commands to download data from kaggle
!kaggle competitions download -c 11785-hw1p2-f24

!unzip -qo /content/11785-hw1p2-f24.zip -d '/content'

100% 3.98G/3.98G [03:29<00:00, 20.2MB/s]
100% 3.98G/3.98G [03:29<00:00, 20.4MB/s]


# Dataset

This section covers the dataset/dataloader class for speech data. You will have to spend time writing code to create this class successfully. We have given you a lot of comments guiding you on what code to write at each stage, from top to bottom of the class. Please try and take your time figuring this out, as it will immensely help in creating dataset/dataloader classes for future homeworks.

Before running the following cells, please take some time to analyse the structure of data. Try loading a single MFCC and its transcipt, print out the shapes and print out the values. Do the transcripts look like phonemes?

In [ ]:
# Dataset class to load train and validation data

class AudioDatasetTrain(torch.utils.data.Dataset):

    def __init__(self, root, phonemes = PHONEMES, context=0, partition= "train-clean-100", fraction= 0.2): # Feel free to add more arguments

        self.context    = context
        self.phonemes   = phonemes

        self.t_mask = T.TimeMasking(time_mask_param = self.context // 2)
        self.f_mask = T.FrequencyMasking(freq_mask_param = 4)

        self.phoneme_map = {p: i for i, p in enumerate(self.phonemes)}

        # TODO: MFCC directory - use partition to acces train/dev directories from kaggle data using root
        self.mfcc_dir       = os.path.join(root, partition, "mfcc")
        # TODO: Transcripts directory - use partition to acces train/dev directories from kaggle data using root
        self.transcript_dir = os.path.join(root, partition, "transcript")

        # TODO: List files in sefl.mfcc_dir using os.listdir in sorted order
        mfcc_names          = sorted(os.listdir(self.mfcc_dir))
        # TODO: List files in self.transcript_dir using os.listdir in sorted order
        transcript_names    = sorted(os.listdir(self.transcript_dir))

        # Making sure that we have the same no. of mfcc and transcripts
        assert len(mfcc_names) == len(transcript_names)

        self.mfccs, self.transcripts = [], []

        # TODO: Iterate through mfccs and transcripts
        for i in range(len(mfcc_names)):
        #   Load a single mfcc
            mfcc            = np.load(os.path.join(self.mfcc_dir, mfcc_names[i]))
        #   Do Cepstral Normalization of mfcc (explained in writeup)
            mean_mfcc   = np.mean(mfcc, axis = 0)
            std_mfcc = np.std(mfcc, axis = 0) + 1e-8
            mfcc  = (mfcc - mean_mfcc) / std_mfcc
        #   Load the corresponding transcript
            transcript      = np.load(os.path.join(self.transcript_dir, transcript_names[i]))[1:-1] # Remove [SOS] and [EOS] from the transcript
            # (Is there an efficient way to do this without traversing through the transcript?)
            # Note that SOS will always be in the starting and EOS at end, as the name suggests.
        #   Append each mfcc to self.mfcc, transcript to self.transcript

            zh_index = np.where(transcript == 'ZH')[0]
            if len(zh_index) > 0:
                self.mfccs.append(mfcc)
                self.transcripts.append(transcript)

            else:
                if np.random.rand() <= fraction:
                    self.mfccs.append(mfcc)
                    self.transcripts.append(transcript)
            # zh_transcript = transcript[zh_index]
            # zh_mfcc = mfcc[zh_index, :]

            # remaining_index = np.setdiff1d(np.arange(len(transcript)- 2), zh_index)
            # sampled_index = np.random.choice(remaining_index, size=int(fraction * len(remaining_index)), replace=False)
            # sampled_transcript = transcript[sampled_index]
            # sampled_mfcc = mfcc[sampled_index, :]

            # final_transcript = np.concatenate((zh_transcript, sampled_transcript), axis = 0)
            # final_mfcc = np.concatenate((zh_mfcc, sampled_mfcc), axis = 0)




            # self.mfccs.append(final_mfcc)
            # self.transcripts.append(final_transcript)

        # NOTE:
        # Each mfcc is of shape T1 x 28, T2 x 28, ...
        # Each transcript is of shape (T1+2), (T2+2) before removing [SOS] and [EOS]



        # TODO: Concatenate all mfccs in self.mfccs such that
        # the final shape is T x 28 (Where T = T1 + T2 + ...)
        self.mfccs          = np.concatenate((self.mfccs), axis = 0)

        # TODO: Concatenate all transcripts in self.transcripts such that
        # the final shape is (T,) meaning, each time step has one phoneme output
        self.transcripts    = np.concatenate((self.transcripts), axis = 0)
        # Hint: Use numpy to concatenate

        # Length of the dataset is now the length of concatenated mfccs/transcripts
        self.length = len(self.mfccs)

        # Take some time to think about what we have done.
        # self.mfcc is an array of the format (Frames x Features).
        # Our goal is to recognize phonemes of each frame
        # We can introduce context by padding zeros on top and bottom of self.mfcc
        self.mfccs = np.concatenate((np.zeros((self.context, 28)), self.mfccs, np.zeros((self.context, 28)))) # TODO

        # The available phonemes in the transcript are of string data type
        # But the neural network cannot predict strings as such.
        # Hence, we map these phonemes to integers

        # TODO: Map the phonemes to their corresponding list indexes in self.phonemes
        self.transcripts = np.array([self.phoneme_map[i] for i in self.transcripts])
        # Now, if an element in self.transcript is 0, it means that it is 'SIL' (as per the above example)

    def __len__(self):
        return self.length

    def __getitem__(self, ind):

        # TODO: Based on context and offset, return a frame at given index with context frames to the left, and right.
        frames = self.mfccs[ind: ind + 2 * self.context + 1,]
        frames = torch.FloatTensor(frames)
        # frames = frames.T
        # frames = self.t_mask(frames)
        # frames = self.f_mask(frames)
        # frames = frames.T
        # After slicing, you get an array of shape 2*context+1 x 28. But our MLP needs 1d data and not 2d.
        frames = frames.flatten() # TODO: Flatten to get 1d data

        # frames      = torch.FloatTensor(frames) # Convert to tensors
        # phonemes    = torch.tensor(self.phoneme_map[self.transcripts[ind]])
        phonemes = torch.tensor(self.transcripts[ind])

        return frames, phonemes

    # def collate_fn(self, batch):
    #     frames, phonemes = zip(*batch)



In [ ]:
# Dataset class to load train and validation data

class AudioDatasetVal(torch.utils.data.Dataset):

    def __init__(self, root, phonemes = PHONEMES, context=0, partition= "dev-clean", transform= None): # Feel free to add more arguments

        self.context    = context
        self.phonemes   = phonemes

        self.t_mask = T.TimeMasking(time_mask_param = self.context // 2)
        self.f_mask = T.FrequencyMasking(freq_mask_param = 4)

        self.phoneme_map = {p: i for i, p in enumerate(self.phonemes)}

        # TODO: MFCC directory - use partition to acces train/dev directories from kaggle data using root
        self.mfcc_dir       = os.path.join(root, partition, "mfcc")
        # TODO: Transcripts directory - use partition to acces train/dev directories from kaggle data using root
        self.transcript_dir = os.path.join(root, partition, "transcript")

        # TODO: List files in sefl.mfcc_dir using os.listdir in sorted order
        mfcc_names          = sorted(os.listdir(self.mfcc_dir))
        # TODO: List files in self.transcript_dir using os.listdir in sorted order
        transcript_names    = sorted(os.listdir(self.transcript_dir))

        # Making sure that we have the same no. of mfcc and transcripts
        assert len(mfcc_names) == len(transcript_names)
        self.mfccs, self.transcripts = [], []

        # TODO: Iterate through mfccs and transcripts
        for i in range(len(mfcc_names)):
        #   Load a single mfcc
            mfcc            = np.load(os.path.join(self.mfcc_dir, mfcc_names[i]))
        #   Do Cepstral Normalization of mfcc (explained in writeup)
            mean_mfcc   = np.mean(mfcc, axis = 0)
            std_mfcc = np.std(mfcc, axis = 0) + 1e-8
            difference  = (mfcc - mean_mfcc) / std_mfcc
        #   Load the corresponding transcript
            transcript      = np.load(os.path.join(self.transcript_dir, transcript_names[i]))[1:-1] # Remove [SOS] and [EOS] from the transcript
            # (Is there an efficient way to do this without traversing through the transcript?)
            # Note that SOS will always be in the starting and EOS at end, as the name suggests.
        #   Append each mfcc to self.mfcc, transcript to self.transcript
            self.mfccs.append(difference)
            self.transcripts.append(transcript)

        # NOTE:
        # Each mfcc is of shape T1 x 28, T2 x 28, ...
        # Each transcript is of shape (T1+2), (T2+2) before removing [SOS] and [EOS]

        ## Stratified sampling
        # for phoneme in self.phonemes[:-2]:
        #     print

        # TODO: Concatenate all mfccs in self.mfccs such that
        # the final shape is T x 28 (Where T = T1 + T2 + ...)
        self.mfccs          = np.concatenate((self.mfccs), axis = 0)

        # TODO: Concatenate all transcripts in self.transcripts such that
        # the final shape is (T,) meaning, each time step has one phoneme output
        self.transcripts    = np.concatenate((self.transcripts), axis = 0)
        # Hint: Use numpy to concatenate

        # Length of the dataset is now the length of concatenated mfccs/transcripts
        self.length = len(self.mfccs)

        # Take some time to think about what we have done.
        # self.mfcc is an array of the format (Frames x Features).
        # Our goal is to recognize phonemes of each frame
        # We can introduce context by padding zeros on top and bottom of self.mfcc
        self.mfccs = np.concatenate((np.zeros((self.context, 28)), self.mfccs, np.zeros((self.context, 28)))) # TODO

        # The available phonemes in the transcript are of string data type
        # But the neural network cannot predict strings as such.
        # Hence, we map these phonemes to integers

        # TODO: Map the phonemes to their corresponding list indexes in self.phonemes

        # Now, if an element in self.transcript is 0, it means that it is 'SIL' (as per the above example)

    def __len__(self):
        return self.length

    def __getitem__(self, ind):

        # TODO: Based on context and offset, return a frame at given index with context frames to the left, and right.
        frames = self.mfccs[ind: ind + 2 * self.context + 1,]

        # After slicing, you get an array of shape 2*context+1 x 28. But our MLP needs 1d data and not 2d.
        frames = frames.flatten() # TODO: Flatten to get 1d data

        frames      = torch.FloatTensor(frames) # Convert to tensors
        phonemes    = torch.tensor(self.phoneme_map[self.transcripts[ind]])

        return frames, phonemes



In [ ]:
class AudioTestDataset(torch.utils.data.Dataset):

    # TODO: Create a test dataset class similar to the previous class but you dont have transcripts for this
    # Imp: Read the mfccs in sorted order, do NOT shuffle the data here or in your dataloader.

    def __init__(self, root, phonemes = PHONEMES, context=0, partition= "test-clean"): # Feel free to add more arguments

        self.context    = context
        self.phonemes   = phonemes

        # TODO: MFCC directory - use partition to acces train/dev directories from kaggle data using root
        self.mfcc_dir   = os.path.join(root, partition, "mfcc")

        # TODO: List files in sefl.mfcc_dir using os.listdir in sorted order
        mfcc_names      = sorted(os.listdir(self.mfcc_dir))

        self.mfccs = []

        # TODO: Iterate through mfccs and transcripts
        for i in range(len(mfcc_names)):
        #   Load a single mfcc
            mfcc        = np.load(os.path.join(self.mfcc_dir, mfcc_names[i]))
        #   Do Cepstral Normalization of mfcc (explained in writeup)
            mean_mfcc   = np.mean(mfcc, axis = 0)
            std_mfcc = np.std(mfcc, axis = 0)
            difference  = (mfcc - mean_mfcc) / std_mfcc
            self.mfccs.append(difference)


        self.mfccs  = np.concatenate((self.mfccs), axis = 0)


        self.length = len(self.mfccs)

        self.mfccs = np.concatenate((np.zeros((self.context, 28)), self.mfccs, np.zeros((self.context, 28)))) # TODO



    def __len__(self):
        return self.length

    def __getitem__(self, ind):

        # TODO: Based on context and offset, return a frame at given index with context frames to the left, and right.
        frames = self.mfccs[ind: ind + 2 * self.context + 1,]
        # After slicing, you get an array of shape 2*context+1 x 28. But our MLP needs 1d data and not 2d.
        frames = frames.flatten() # TODO: Flatten to get 1d data

        frames = torch.FloatTensor(frames) # Convert to tensors


        return frames



# Parameters Configuration

Storing your parameters and hyperparameters in a single configuration dictionary makes it easier to keep track of them during each experiment. It can also be used with weights and biases to log your parameters for each experiment and keep track of them across multiple experiments.

In [ ]:
config = {
    'epochs'        : 10,
    'batch_size'    : 4096,
    'context'       : 20,
    'init_lr'       : 1e-3,
    'architecture'  : 'very-low-cutoff'
    # Add more as you need them - e.g dropout values, weight decay, scheduler parameters\
}

In [ ]:
config = {
    'epochs'        : 50,
    'batch_size'    : 1024,
    'context'       : 25,
    'init_lr'       : 0.01,

    # model
    'architecture'  : 'NormNet',
    'dropout'       : 0.15,
    'hidden_layers' : 3,
    'funnel_layers' : 3,
    'time_mask'     : 7,
    'frequency_mask': 3,
    'layer_size'    : 2048,

    # 'architecture'  : 'ExpandedNormNet',
    # 'dropout'       : 0.2,
    # 'expansion_layers' : 1,
    # 'hidden_layers' : 1,
    # 'funnel_layers' : 5,
    # 'time_mask'     : 7,
    # 'frequency_mask': 3,
    # 'layer_size'    : 2048,

    # 'architecture'  : 'ResNet',
    # 'dropout'       : 0.15,
    # 'time_mask'     : 10,
    # 'frequency_mask': 3,
    # 'layer_size'    : 2048,


    # 'architecture'  : 'InceptionNet',
    # 'dropout'       : 0.15,
    # 'time_mask'     : 10,
    # 'frequency_mask': 3,
    # 'layer_size'    : 512,
    # 'hidden_layers' : 14,
    # 'residual'      : 2,


    ### Activation functions
    # 'activation'    : 'ReLU',

    'activation'    : 'LeakyReLU',
    'negative_slope': 0.01,

    ## scheduler

    ## StepLR
    # 'scheduler'     : 'StepLR',
    # 'step_size'     : 5,
    # 'gamma'         : 0.1,

    ## CosineAnnealing
    # 'scheduler'     : 'CS',
    # 'T_max'         : 15,
    # 'final_lr'      : 0.0001,


    ## CosineAnnealingWithWarmRestarts
    'scheduler'     : 'CSWR',
    'final_lr'      : 0.0001,
    'T_0'           : 10,
    'T_mult'        : 1,

    ## optimizer
    'optimizer'     : 'Adam'
    # 'weight_decay'  : 0.01

    # 'optimizer'     : 'Rprop'

    ## weight initialization

    ##

}

# Create Datasets

In [ ]:
train_data = None
val_data = None
test_data = None

In [ ]:
#TODO: Create a dataset object using the AudioDataset class for the training data
# def __init__(self, root, phonemes = PHONEMES, context=0, partition= "train-clean-100"): # Feel free to add more arguments
train_data = AudioDatasetTrain(root = "/content/11785-f24-hw1p2", phonemes= PHONEMES, context= config['context'], partition= "train-clean-100", fraction= 1)

# TODO: Create a dataset object using the AudioDataset class for the validation data
val_data = AudioDatasetVal(root = "/content/11785-f24-hw1p2", phonemes= PHONEMES, context= config['context'], partition= "dev-clean")

# TODO: Create a dataset object using the AudioTestDataset class for the test data
test_data = AudioTestDataset(root = "/content/11785-f24-hw1p2", phonemes= PHONEMES, context= config['context'], partition= "test-clean")

In [ ]:
# count = {i: 0 for i, p in enumerate(PHONEMES[:-2])}
# for mfcc, transcript in train_data:
#     # count[transcript] += 1
#     # print(X)
#     count[transcript.item()] += 1

# count

In [ ]:
# Define dataloaders for train, val and test datasets
# Dataloaders will yield a batch of frames and phonemes of given batch_size at every iteration
# We shuffle train dataloader but not val & test dataloader. Why?

train_loader = torch.utils.data.DataLoader(
    dataset     = train_data,
    num_workers = 4,
    batch_size  = config['batch_size'],
    pin_memory  = True,
    shuffle     = True

)

val_loader = torch.utils.data.DataLoader(
    dataset     = val_data,
    num_workers = 1,
    batch_size  = config['batch_size'],
    pin_memory  = True,
    shuffle     = False

)

test_loader = torch.utils.data.DataLoader(
    dataset     = test_data,
    num_workers = 1,
    batch_size  = config['batch_size'],
    pin_memory  = True,
    shuffle     = False
)


print("Batch size     : ", config['batch_size'])
print("Context        : ", config['context'])
print("Input size     : ", (2*config['context']+1)*28)
print("Output symbols : ", len(PHONEMES))

print("Train dataset samples = {}, batches = {}".format(train_data.__len__(), len(train_loader)))
print("Validation dataset samples = {}, batches = {}".format(val_data.__len__(), len(val_loader)))
print("Test dataset samples = {}, batches = {}".format(test_data.__len__(), len(test_loader)))

Batch size     :  1024
Context        :  25
Input size     :  1428
Output symbols :  40
Train dataset samples = 36091157, batches = 35246
Validation dataset samples = 1928204, batches = 1884
Test dataset samples = 1934138, batches = 1889


In [ ]:
# Testing code to check if your data loaders are working
for i, data in enumerate(train_loader):
    frames, phoneme = data
    print(frames.shape, phoneme.shape)
    break

torch.Size([1024, 1428]) torch.Size([1024])


# Configuration

# Network Architecture


This section defines your network architecture for the homework. We have given you a sample architecture that can easily clear the very low cutoff for the early submission deadline.

In [ ]:
# This architecture will make you cross the very low cutoff
# However, you need to run a lot of experiments to cross the medium or high cutoff
class Network(torch.nn.Module):

    def __init__(self, input_size, output_size):
        super(Simplelayer, self).__init__()
        if config['activation'] == 'ReLU':
            self.activation = torch.nn.ReLU()
        elif config['activation'] == 'LeakyReLU':
            self.activation = torch.nn.LeakyReLU(negative_slope= config['negative_slope'])

        self.layer = torch.nn.Sequential(
            torch.nn.Linear(input_size, output_size),
            torch.nn.BatchNorm1d(output_size),
            self.activation,
            torch.nn.Dropout(dropout)
        )

    def forward(self, x):
        return self.layer(x)

In [ ]:
class BetterNet(torch.nn.Module):
    def __init__(self, input_size, context, output_size, hidden_layers= 2):
        super(BetterNet, self).__init__()
        self.hidden_size = (2 * context + 1) * output_size

        # Create a list to hold the layers
        layers = []

        # Add the first layer (input -> hidden_size)
        layers.append(torch.nn.Linear(input_size, self.hidden_size))
        layers.append(torch.nn.ReLU())

        # Add the hidden layers
        for _ in range(hidden_layers):
            layers.append(torch.nn.Linear(self.hidden_size, self.hidden_size))
            layers.append(torch.nn.ReLU())

        # Add the output layer (hidden_size -> output_size)
        layers.append(torch.nn.Linear(self.hidden_size, output_size))

        # Use Sequential to stack all layers
        self.model = torch.nn.Sequential(*layers)

    def forward(self, x):
        out = self.model(x)
        return out

In [ ]:
class SuperNet(torch.nn.Module):
    def __init__(self, input_size, context, output_size, hidden_layers= 2):
        super(SuperNet, self).__init__()
        self.hidden_size = (2 * context + 1) * output_size

        # Create a list to hold the layers
        layers = []

        # Add the first layer (input -> hidden_size)
        layers.append(torch.nn.Linear(input_size, self.hidden_size))
        layers.append(torch.nn.ReLU())

        # Add the hidden layers
        for _ in range(hidden_layers):
            layers.append(torch.nn.Linear(self.hidden_size, self.hidden_size))
            layers.append(torch.nn.ReLU())

        # Add the output layer (hidden_size -> output_size)
        layers.append(torch.nn.Linear(self.hidden_size, self.hidden_size // 2))
        layers.append(torch.nn.ReLU())
        layers.append(torch.nn.Linear(self.hidden_size // 2, self.hidden_size // 2))
        layers.append(torch.nn.ReLU())
        layers.append(torch.nn.Linear(self.hidden_size // 2, output_size))

        # layers.append(torch.nn.Softmax(dim=1))
        # Use Sequential to stack all layers
        self.model = torch.nn.Sequential(*layers)

    def forward(self, x):
        out = self.model(x)
        return out

In [ ]:
class NormNet(torch.nn.Module):
    def __init__(self, input_size, output_size, context, hidden_layers= 3, funnel_layers=3, dropout_prob=0.5):

        super(NormNet, self).__init__()

        self.t_mask = T.TimeMasking(config['time_mask'], iid_masks= True)
        self.f_mask = T.FrequencyMasking(config['frequency_mask'], iid_masks= True)

        if config['activation'] == 'ReLU':
            self.activation = torch.nn.ReLU()
        elif config['activation'] == 'LeakyReLU':
            self.activation = torch.nn.LeakyReLU(negative_slope= config['negative_slope'])

        # Initialize the width of the first layer
        layer_size = config['layer_size']

        # Create a list to hold the layers
        layers = []

        # Add the first layer (input -> 1024)
        layers.append(torch.nn.Linear(input_size, layer_size))
        layers.append(torch.nn.BatchNorm1d(layer_size))
        layers.append(self.activation)
        layers.append(torch.nn.Dropout(dropout_prob))

        for _ in range(hidden_layers):
            layers.append(torch.nn.Linear(layer_size, layer_size))
            layers.append(torch.nn.BatchNorm1d(layer_size))
            layers.append(self.activation)
            layers.append(torch.nn.Dropout(dropout_prob))

        # Add the hidden layers, progressively decreasing in size
        for _ in range(funnel_layers):
            next_layer_size = layer_size // 2  # Reduce layer width for the funnel effect
            layers.append(torch.nn.Linear(layer_size, next_layer_size))
            layers.append(torch.nn.BatchNorm1d(next_layer_size))
            layers.append(self.activation)
            layers.append(torch.nn.Dropout(dropout_prob))
            layer_size = next_layer_size  # Update current layer size to the next layer size

        # Add the final output layer (smaller hidden -> output_size)
        layers.append(torch.nn.Linear(layer_size, output_size))

        # Use Sequential to stack all layers
        self.model = torch.nn.Sequential(*layers)

    def forward(self, x):
        if self.training:
            b = x.shape[0]
            o = x.shape[1]

            t = x.numel()

            x = x.contiguous().view(b, t // (b * 28), 28)
            x = x.transpose(1,2)

            x = self.t_mask(x)
            x = self.f_mask(x)

            x = x.transpose(1,2)

            x = x.contiguous().view(b, o)

        return self.model(x)


In [ ]:
class ExpandedNormNet(torch.nn.Module):
    def __init__(self, input_size, output_size, context, expansion_layers= 2, hidden_layers= 3, funnel_layers=3, dropout_prob=0.5):

        super(ExpandedNormNet, self).__init__()

        self.t_mask = T.TimeMasking(config['time_mask'], iid_masks= True)
        self.f_mask = T.FrequencyMasking(config['frequency_mask'], iid_masks= True)

        if config['activation'] == 'ReLU':
            self.activation = torch.nn.ReLU()
        elif config['activation'] == 'LeakyReLU':
            self.activation = torch.nn.LeakyReLU(negative_slope= config['negative_slope'])

        # Initialize the width of the first layer
        layer_size = config['layer_size']

        # Create a list to hold the layers
        layers = []

        layers.append(torch.nn.Linear(input_size, 2 * layer_size))
        layers.append(torch.nn.BatchNorm1d(2 *layer_size))
        layers.append(self.activation)
        layers.append(torch.nn.Dropout(dropout_prob))

        for _ in range(expansion_layers - 1):
            layers.append(torch.nn.Linear(2 * layer_size, 2 * layer_size))
            layers.append(torch.nn.BatchNorm1d(2 *layer_size))
            layers.append(self.activation)
            layers.append(torch.nn.Dropout(dropout_prob))

        layers.append(torch.nn.Linear(2 * layer_size, layer_size))
        layers.append(torch.nn.BatchNorm1d(layer_size))
        layers.append(self.activation)
        layers.append(torch.nn.Dropout(dropout_prob))

        for _ in range(hidden_layers - 1):
            layers.append(torch.nn.Linear(layer_size, layer_size))
            layers.append(torch.nn.BatchNorm1d(layer_size))
            layers.append(self.activation)
            layers.append(torch.nn.Dropout(dropout_prob))

        # Add the hidden layers, progressively decreasing in size
        for _ in range(funnel_layers):
            next_layer_size = layer_size // 2  # Reduce layer width for the funnel effect
            layers.append(torch.nn.Linear(layer_size, next_layer_size))
            layers.append(torch.nn.BatchNorm1d(next_layer_size))
            layers.append(self.activation)
            layers.append(torch.nn.Dropout(dropout_prob))
            layer_size = next_layer_size  # Update current layer size to the next layer size

        # Add the final output layer (smaller hidden -> output_size)
        layers.append(torch.nn.Linear(layer_size, output_size))

        # Use Sequential to stack all layers
        self.model = torch.nn.Sequential(*layers)

    def forward(self, x):
        if self.training:
            b = x.shape[0]
            o = x.shape[1]

            t = x.numel()

            x = x.contiguous().view(b, t // (b * 28), 28)
            x = x.transpose(1,2)

            x = self.t_mask(x)
            x = self.f_mask(x)

            x = x.transpose(1,2)

            x = x.contiguous().view(b, o)

        return self.model(x)


In [ ]:
class SimpleLayer(torch.nn.Module):
    def __init__(self, input_size, output_size, dropout):
        super(SimpleLayer, self).__init__()
        if config['activation'] == 'ReLU':
            self.activation = torch.nn.ReLU()
        elif config['activation'] == 'LeakyReLU':
            self.activation = torch.nn.LeakyReLU(negative_slope= config['negative_slope'])

        self.layer = torch.nn.Sequential(
            torch.nn.Linear(input_size, output_size),
            torch.nn.BatchNorm1d(output_size),
            self.activation,
            torch.nn.Dropout(dropout)
        ).to(device)

    def forward(self, x):
        return self.layer(x)

In [ ]:
class InceptionModel(torch.nn.Module):
    def __init__(self, input_size, output_size, context, hidden_layers= 3, residual= 2, dropout_prob=0.5):
        super(InceptionModel, self).__init__()
        self.t_mask = T.TimeMasking(config['time_mask'], iid_masks= True)
        self.f_mask = T.FrequencyMasking(config['frequency_mask'], iid_masks= True)

        self.layers = []
        self.hidden_layers = hidden_layers
        self.residual = residual
        self.layers.append(SimpleLayer(input_size,
                                       2 * config['layer_size'],
                                       dropout_prob).to(device))

        for _ in range(hidden_layers):
            self.layers.append(SimpleLayer(2 * config['layer_size'],
                                           2 * config['layer_size'],
                                           dropout_prob).to(device))

        self.layers.append(torch.nn.Linear(2*config['layer_size'],
                                           output_size).to(device))


        self.model = torch.nn.Sequential(*self.layers)


    def forward(self, x):
        if self.training:
            b = x.shape[0]
            o = x.shape[1]

            t = x.numel()

            x = x.contiguous().view(b, t // (b * 28), 28)
            x = x.transpose(1,2)

            x = self.t_mask(x)
            x = self.f_mask(x)

            x = x.transpose(1,2)

            x = x.contiguous().view(b, o)

        f = self.layers[0](x)
        res = []
        for i in range(3, self.hidden_layers):
            if i <= self.residual:
              res.append(f)
            if i >= self.hidden_layers - self.residual:
                f = f + self.layers[i](f)
            else:
                f = self.layers[i](f)

        return self.layers[-1](f)


In [ ]:
class ResNet(torch.nn.Module):
    def __init__(self, input_size, output_size, context, dropout_prob=0.5):
        super(ResNet, self).__init__()

        self.t_mask = T.TimeMasking(config['time_mask'], iid_masks= True)
        self.f_mask = T.FrequencyMasking(config['frequency_mask'], iid_masks= True)

        if config['activation'] == 'ReLU':
            self.activation = torch.nn.ReLU()
        elif config['activation'] == 'LeakyReLU':
            self.activation = torch.nn.LeakyReLU(negative_slope= config['negative_slope'])

        self.fc1 = torch.nn.Linear(input_size, config['layer_size']).to(device)
        self.fc2 = torch.nn.Linear(config['layer_size'], config['layer_size']).to(device)
        self.fc3 = torch.nn.Linear(config['layer_size'], config['layer_size']).to(device)
        self.fc4 = torch.nn.Linear(config['layer_size'], config['layer_size']).to(device)
        self.fc5 = torch.nn.Linear(config['layer_size'], config['layer_size']).to(device)
        self.fc6 = torch.nn.Linear(config['layer_size'], output_size).to(device)

        self.bn1 = torch.nn.BatchNorm1d(config['layer_size']).to(device)
        self.bn2 = torch.nn.BatchNorm1d(config['layer_size']).to(device)
        self.bn3 = torch.nn.BatchNorm1d(config['layer_size']).to(device)
        self.bn4 = torch.nn.BatchNorm1d(config['layer_size']).to(device)
        self.bn5 = torch.nn.BatchNorm1d(config['layer_size']).to(device)

        self.dropout = torch.nn.Dropout(dropout_prob).to(device)



    def forward(self, x):
        if self.training:
            b = x.shape[0]
            o = x.shape[1]

            t = x.numel()

            x = x.contiguous().view(b, t // (b * 28), 28)
            x = x.transpose(1,2)

            x = self.t_mask(x)
            x = self.f_mask(x)

            x = x.transpose(1,2)

            x = x.contiguous().view(b, o)


        o1 = self.dropout(self.activation(self.bn1(self.fc1(x))))
        o2 = self.dropout(self.activation(self.bn2(self.fc2(o1))))
        o3 = self.dropout(self.activation(self.bn3(self.fc3(o2)))) + o2
        o4 = self.dropout(self.activation(self.bn4(self.fc4(o3))))
        o5 = self.dropout(self.activation(self.bn5(self.fc5(o4)))) + o4

        o6 = self.fc6(o5)

        return o6

In [ ]:
m = ResNet((config['context'] * 2 + 1) * 28, len(PHONEMES), config['context']).to(device)
m(frames.to(device))

tensor([[-0.5059, -0.2526, -1.7765,  ..., -1.2396,  0.9300, -1.3776],
        [ 1.3824, -0.5681, -0.9655,  ...,  0.2117, -1.0676, -0.4105],
        [-0.4488,  0.0114, -0.3409,  ...,  0.5808, -0.8281,  0.2072],
        ...,
        [ 0.9447, -1.4383, -0.1584,  ...,  1.0837,  0.1121, -0.9424],
        [ 0.1986, -0.2856,  0.5892,  ..., -0.0154,  1.1355, -0.7734],
        [-1.6066, -1.6623, -0.4556,  ...,  1.3461, -0.1301, -1.3468]],
       device='cuda:0', grad_fn=<AddmmBackward0>)

# Define Model, Loss Function and Optimizer

Here we define the model, loss function, optimizer and optionally a learning rate scheduler.

In [ ]:
model = None

In [ ]:
INPUT_SIZE  = (2*config['context'] + 1) * 28 # Why is this the case?
OUTPUT_SIZE = len(PHONEMES)

if config['architecture'] == 'Network':
    model = Network(INPUT_SIZE,
                    OUTPUT_SIZE).to(device)

elif config['architecture'] == 'BetterNet':
    model = BetterNet(INPUT_SIZE,
                      config['context'],
                      OUTPUT_SIZE,
                      config['hidden_layers']).to(device)

elif config['architecture'] == 'SuperNet':
    model = SuperNet(INPUT_SIZE,
                    config['context'],
                    OUTPUT_SIZE,
                    config['hidden_layers']).to(device)

elif config['architecture'] == 'ExpandedNormNet':
    model = ExpandedNormNet(INPUT_SIZE,
                            OUTPUT_SIZE,
                            config['context'],
                            expansion_layers= config['expansion_layers'],
                            hidden_layers= config['hidden_layers'],
                            funnel_layers = config['funnel_layers'],
                            dropout_prob = config['dropout']).to(device)

elif config['architecture'] == 'InceptionNet':
    model = InceptionModel(INPUT_SIZE,
                           OUTPUT_SIZE,
                           config['context'],
                           config['hidden_layers'],
                           config['residual'],
                           config['dropout']).to(device)

elif config['architecture'] == 'ResNet':
    model = ResNet(INPUT_SIZE,
                   OUTPUT_SIZE,
                   config['context'],
                   config['dropout']).to(device)

else:
    model = NormNet(INPUT_SIZE,
                    OUTPUT_SIZE,
                    config['context'],
                    hidden_layers= config['hidden_layers'],
                    funnel_layers= config['funnel_layers'],
                    dropout_prob= config['dropout']).to(device)


summary(model, frames.to(device))
# Check number of parameters of your network
# Remember, you are limited to 20 million parameters for HW1 (including ensembles)

----------------------------------------------------------------------------------------------------
Layer                   Kernel Shape         Output Shape         # Params (K)      # Mult-Adds (M)
0_TimeMasking                      -       [1024, 28, 51]                    -                    -
1_FrequencyMasking                    -       [1024, 28, 51]                    -                    -
2_Linear                [1428, 2048]         [1024, 2048]             2,926.59                 2.92
3_BatchNorm1d                 [2048]         [1024, 2048]                 4.10                 0.00
4_LeakyReLU                        -         [1024, 2048]                    -                    -
5_LeakyReLU                        -         [1024, 2048]                    -                    -
6_Dropout                          -         [1024, 2048]                    -                    -
7_Linear                [2048, 2048]         [1024, 2048]             4,196.35                 4

In [ ]:
next(model.parameters()).is_cuda

True

In [ ]:
# t_mask = T.TimeMasking(time_mask_param = config['time_mask'])
# f_mask = T.FrequencyMasking(freq_mask_param = config['frequency_mask'])

# for frames, phonemes in train_loader:

#     frames = frames.contiguous().view(config['batch_size'], 2 * config['context'] + 1, 28)
#     frames = frames.transpose(1,2)

#     frames = t_mask(frames)
#     frames = f_mask(frames)

#     frames = frames.transpose(1,2)

#     frames = frames.contiguous().view(config['batch_size'], INPUT_SIZE)

#     break

In [ ]:
criterion = torch.nn.CrossEntropyLoss() # Defining Loss function.
# We use CE because the task is multi-class classification

#Defining Optimizer
if config['optimizer'] == 'Adam':
    optimizer = torch.optim.Adam(model.parameters(),
                                 lr= config['init_lr'])
elif config['optimizer'] == 'Rprop':
    optimizer = torch.optim.Rprop(model.parameters(), lr = config['init_lr'])
# Recommended : Define Scheduler for Learning Rate,
# including but not limited to StepLR, MultiStep, CosineAnnealing, CosineAnnealingWithWarmRestarts, ReduceLROnPlateau, etc.
# You can refer to Pytorch documentation for more information on how to use them.
if config['scheduler'] == 'StepLR':
    scheduler = torch.optim.lr_scheduler.StepLR(optimizer,
                                                config['step_size'],
                                                config['gamma'])

elif config['scheduler'] == 'CSWR':
    scheduler = torch.optim.lr_scheduler.CosineAnnealingWarmRestarts(optimizer,
                                                                     config['T_0'],
                                                                     T_mult=1,
                                                                     eta_min=config['final_lr'])

elif config['scheduler'] == 'CS':
    scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer,
                                                           T_max = config['T_max'],
                                                           eta_min=config['final_lr'])
# Is your training time very high?
# Look into mixed precision training if your GPU (Tesla T4, V100, etc) can make use of it
# Refer - https://pytorch.org/docs/stable/notes/amp_examples.html

# Training and Validation Functions

This section covers the training, and validation functions for each epoch of running your experiment with a given model architecture. The code has been provided to you, but we recommend going through the comments to understand the workflow to enable you to write these loops for future HWs.

In [ ]:
torch.cuda.empty_cache()
gc.collect()

119

In [ ]:
def train(model, dataloader, optimizer, criterion, scaler= None):

    model.train()
    tloss, tacc = 0, 0 # Monitoring loss and accuracy
    batch_bar   = tqdm(total=len(train_loader), dynamic_ncols=True, leave=False, position=0, desc='Train')

    for i, (frames, phonemes) in enumerate(dataloader):

        ### Initialize Gradients
        optimizer.zero_grad()

        ### Move Data to Device (Ideally GPU)
        frames      = frames.to(device)
        phonemes    = phonemes.to(device)

        if scaler:
            with autocast(device_type='cuda', dtype=torch.float16):
                logits = model(frames)
                loss = criterion(logits, phonemes)

            scaler.scale(loss).backward()
            scaler.step(optimizer)
            scaler.update()

        else:
            ### Forward Propagation
            logits  = model(frames)

            ### Loss Calculation
            loss    = criterion(logits, phonemes)

            ### Backward Propagation
            loss.backward()

            ### Gradient Descent
            optimizer.step()



        tloss   += loss.item()
        tacc    += torch.sum(torch.argmax(logits, dim= 1) == phonemes).item()/logits.shape[0]

        batch_bar.set_postfix(loss="{:.04f}".format(float(tloss / (i + 1))),
                              acc="{:.04f}%".format(float(tacc*100 / (i + 1))))
        batch_bar.update()

        ### Release memory
        del frames, phonemes, logits
        torch.cuda.empty_cache()

    batch_bar.close()
    tloss   /= len(train_loader)
    tacc    /= len(train_loader)

    return tloss, tacc

In [ ]:
def eval(model, dataloader):

    model.eval() # set model in evaluation mode
    vloss, vacc = 0, 0 # Monitoring loss and accuracy
    batch_bar   = tqdm(total=len(val_loader), dynamic_ncols=True, position=0, leave=False, desc='Val')

    for i, (frames, phonemes) in enumerate(dataloader):

        ### Move data to device (ideally GPU)
        frames      = frames.to(device)
        phonemes    = phonemes.to(device)

        # makes sure that there are no gradients computed as we are not training the model now
        with torch.inference_mode():
            ### Forward Propagation
            logits  = model(frames)
            ### Loss Calculation
            loss    = criterion(logits, phonemes)

        vloss   += loss.item()
        vacc    += torch.sum(torch.argmax(logits, dim= 1) == phonemes).item()/logits.shape[0]

        # Do you think we need loss.backward() and optimizer.step() here?

        batch_bar.set_postfix(loss="{:.04f}".format(float(vloss / (i + 1))),
                              acc="{:.04f}%".format(float(vacc*100 / (i + 1))))
        batch_bar.update()

        ### Release memory
        del frames, phonemes, logits
        torch.cuda.empty_cache()

    batch_bar.close()
    vloss   /= len(val_loader)
    vacc    /= len(val_loader)

    return vloss, vacc

# Weights and Biases Setup

This section is to enable logging metrics and files with Weights and Biases. Please refer to wandb documentationa and recitation 0 that covers the use of weights and biases for logging, hyperparameter tuning and monitoring your runs for your homeworks. Using this tool makes it very easy to show results when submitting your code and models for homeworks, and also extremely useful for study groups to organize and run ablations under a single team in wandb.

We have written code for you to make use of it out of the box, so that you start using wandb for all your HWs from the beginning.

In [ ]:
wandb.login(key="6e6412a1eff673cacdcda973f6e61422daaa9387") #API Key is in your wandb account, under settings (wandb.ai/settings)

wandb: Using wandb-core as the SDK backend. Please refer to https://wandb.me/wandb-core for more information.
wandb: W&B API key is configured. Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [ ]:
# Create your wandb run
run = wandb.init(
    name    = '__'.join(parameter + '_' + str(config[parameter]) for parameter in config), ### Wandb creates random run names if you skip this field, we recommend you give useful names
    reinit  = True, ### Allows reinitalizing runs when you re-run this cell
    #id     = "y28t31uz", ### Insert specific run id here if you want to resume a previous run
    #resume = "must", ### You need this to resume previous runs, but comment out reinit = True when using this
    project = "hw1p2", ### Project should be created in your wandb account
    config  = config ### Wandb Config for your run
)

In [ ]:
### Save your model architecture as a string with str(model)
model_arch  = str(model)

### Save it in a txt file
arch_file   = open("model_arch.txt", "w")
file_write  = arch_file.write(model_arch)
arch_file.close()

### log it in your wandb run with wandb.save()
wandb.save('model_arch.txt')

['/content/wandb/run-20240919_192708-b1ymnh1r/files/model_arch.txt']

# Experiment

Now, it is time to finally run your ablations! Have fun!

In [ ]:
from google.colab import drive

# Mount your Google Drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# Iterate over number of epochs to train and evaluate your model


torch.cuda.empty_cache()
gc.collect()
wandb.watch(model, log="all")

if device != 'cpu':
    scaler = GradScaler()
    print(scaler)

prev_val_acc = 0
for epoch in range(config['epochs']):

    print("\nEpoch {}/{}".format(epoch+1, config['epochs']))

    curr_lr                 = float(optimizer.param_groups[0]['lr'])
    train_loss, train_acc   = train(model, train_loader, optimizer, criterion, scaler if device != 'cpu' else None)
    scheduler.step()
    val_loss, val_acc       = eval(model, val_loader)

    print("\tTrain Acc {:.04f}%\tTrain Loss {:.04f}\t Learning Rate {:.07f}".format(train_acc*100, train_loss, curr_lr))
    print("\tVal Acc {:.04f}%\tVal Loss {:.04f}".format(val_acc*100, val_loss))

    ### Log metrics at each epoch in your run
    # Optionally, you can log at each batch inside train/eval functions
    # (explore wandb documentation/wandb recitation)
    wandb.log({'train_acc': train_acc*100, 'train_loss': train_loss,
               'val_acc': val_acc*100, 'valid_loss': val_loss, 'lr': curr_lr})

    ### Highly Recommended: Save checkpoint in drive and/or wandb if accuracy is better than your current best
    if val_acc > prev_val_acc:
        torch.save(model.state_dict(), f"/content/drive/MyDrive/HW1P2/bestModel_{epoch}.pt")
        prev_val_acc = val_acc




Epoch 1/50


Train:   0%|          | 0/35246 [00:00<?, ?it/s]

Val:   0%|          | 0/1884 [00:00<?, ?it/s]

	Train Acc 71.1840%	Train Loss 0.9184	 Learning Rate 0.0100000
	Val Acc 79.4873%	Val Loss 0.6198

Epoch 2/50


Train:   0%|          | 0/35246 [00:00<?, ?it/s]

...

Train:   0%|          | 0/35246 [00:00<?, ?it/s]

Val:   0%|          | 0/1884 [00:00<?, ?it/s]

	Train Acc 77.6825%	Train Loss nan	 Learning Rate 0.0097577
	Val Acc 16.6347%	Val Loss nan

Epoch 33/50


Train:   0%|          | 0/35246 [00:00<?, ?it/s]

KeyboardInterrupt: 

# Testing and submission to Kaggle

Before we get to the following code, make sure to see the format of submission given in *sample_submission.csv*. Once you have done so, it is time to fill the following function to complete your inference on test data. Refer the eval function from previous cells to get an idea of how to go about completing this function.

In [ ]:
model.load_state_dict(torch.load('/content/drive/MyDrive/HW1P2/bestModel_29.pt'))

<ipython-input-41-6ef350cd91be>:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load('/content/drive/MyDrive/HW1P2/bestModel_29.pt'))


<All keys matched successfully>

In [ ]:
reverse_phoneme_map = {i: p for i, p in enumerate(PHONEMES)}

In [ ]:
def test(model, test_loader):
    ### What you call for model to perform inference?
    model.eval() # TODO train or eval?

    ### List to store predicted phonemes of test data
    test_predictions = []

    ### Which mode do you need to avoid gradients?
    with torch.inference_mode(): # TODO

        for i, mfccs in enumerate(tqdm(test_loader)):

            mfccs   = mfccs.to(device)

            logits  = model(mfccs)

            ### Get most likely predicted phoneme with argmax

            predicted_phonemes = np.argmax(logits.cpu().numpy(), axis= -1)

            ### How do you store predicted_phonemes with test_predictions? Hint, look at eval
            # TODO
            test_predictions.extend(predicted_phonemes.tolist())

    return test_predictions

In [ ]:
predictions = test(model, test_loader)
print(predictions)

  0%|          | 0/1889 [00:00<?, ?it/s]

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 16, 16, 16, 16, 16, 16, 16, 16, 18, 18, 18, 18, 18, 18, 18, 16, 16, 16, 16, 16, 16, 16, 16, 25, 25, 25, 25, 25, 25, 25, 25, 25, 25, 25, 25, 27, 27, 27, 27, 27, 27, 27, 27, 27, 31, 31, 31, 31, 34, 10, 10, 10, 10, 10, 10, 11, 11, 11, 28, 28, 28, 28, 28, 36, 36, 36, 36, 36, 36, 36, 33, 33, 33, 33, 33, 33, 9, 9, 9, 9, 9, 7, 7, 7, 7, 7, 18, 18, 18, 18, 18, 18, 18, 18, 29, 29, 29, 29, 29, 29, 29, 29, 29, 29, 29, 29, 29, 29, 31, 31, 31, 31, 31, 31, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 34, 14, 14, 14, 14, 14, 14, 14, 14, 35, 28, 28, 12, 12, 3, 3, 9, 9, 9, 9, 9, 9, 9, 17, 17, 17, 17, 17, 17, 23, 23, 23, 23, 23, 23, 23, 23, 12, 12, 12, 12, 12, 12, 12, 12, 12, 12, 12, 12, 12, 28, 12, 12, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 31, 31, 31, 31, 31, 31, 31, 31, 31, 12, 12, 12, 12, 12, 12,

In [ ]:
### Create CSV file with predictions
with open("./submission.csv", "w+") as f:
    f.write("id,label\n")
    for i in range(len(predictions)):
        f.write("{},{}\n".format(i, reverse_phoneme_map[predictions[i]]))

In [ ]:
### Finish your wandb run
run.finish()

In [ ]:
### Submit to kaggle competition using kaggle API (Uncomment below to use)
!kaggle competitions submit -c 11785-hw1p2-f24 -f ./submission.csv -m "second submission"

### However, its always safer to download the csv file and then upload to kaggle

100% 19.3M/19.3M [00:03<00:00, 6.00MB/s]
Successfully submitted to 11785 HW1P2 Fall 2024

### Save your best model


In [ ]:
torch.save(model.state_dict(), "bestModel.pt")

In [ ]:
from google.colab import files

# Replace 'your_file.txt' with the file you want to download
files.download('bestModel.pt')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>